In [0]:
from pyspark.sql.functions import sum, col, when

In [0]:
# dbutils.fs.mount(
#     source = "wasbs://raw-data@azureeastus2st.blob.core.windows.net/",
#     mount_point = "/mnt/raw-data",
#     extra_configs = {"fs.azure.account.key.azureeastus2st.blob.core.windows.net" : dbutils.secrets.get(
#         "databricksScope", "qarsme"
#     )}
# )

dbutils.fs.mount(
    source = "wasbs://transformed-data@azureeastus2st.blob.core.windows.net/",
    mount_point = "/mnt/transformed-data",
    extra_configs = {"fs.azure.account.key.azureeastus2st.blob.core.windows.net" : dbutils.secrets.get(
        "databricksScope", "qarsme"
    )}
)

True

In [0]:
dbutils.fs.ls("/mnt/raw-data")

[FileInfo(path='dbfs:/mnt/raw-data/accounts.csv', name='accounts.csv', size=4670, modificationTime=1764545467000),
 FileInfo(path='dbfs:/mnt/raw-data/data_dictionary.csv', name='data_dictionary.csv', size=996, modificationTime=1764545483000),
 FileInfo(path='dbfs:/mnt/raw-data/products.csv', name='products.csv', size=171, modificationTime=1764545545000),
 FileInfo(path='dbfs:/mnt/raw-data/sales_pipeline.csv', name='sales_pipeline.csv', size=637773, modificationTime=1764545568000),
 FileInfo(path='dbfs:/mnt/raw-data/sales_teams.csv', name='sales_teams.csv', size=1284, modificationTime=1764545585000)]

In [0]:
dbutils.fs.ls("/mnt/transformed-data")

[]

In [0]:
accounts_df = spark.read.format("csv").option("header", "true").option("inferSchema", "true").load("/mnt/raw-data/accounts.csv")
data_dictionary_df = spark.read.format("csv").option("header", "true").option("inferSchema", "true").load("/mnt/raw-data/data_dictionary.csv")
products_df = spark.read.format("csv").option("header", "true").option("inferSchema", "true").load("/mnt/raw-data/products.csv")
sales_pipeline_df = spark.read.format("csv").option("header", "true").option("inferSchema", "true").load("/mnt/raw-data/sales_pipeline.csv")
sales_teams_df = spark.read.format("csv").option("header", "true").option("inferSchema", "true").load("/mnt/raw-data/sales_teams.csv")
accounts_df.show(2)

+----------------+---------+----------------+-------+---------+---------------+-------------+
|         account|   sector|year_established|revenue|employees|office_location|subsidiary_of|
+----------------+---------+----------------+-------+---------+---------------+-------------+
|Acme Corporation|technolgy|            1996|1100.04|     2822|  United States|         NULL|
|      Betasoloin|  medical|            1999| 251.41|      495|  United States|         NULL|
+----------------+---------+----------------+-------+---------+---------------+-------------+
only showing top 2 rows


In [0]:
print(accounts_df.columns)
print(data_dictionary_df.columns)
print(products_df.columns)
print(sales_pipeline_df.columns)
print(sales_teams_df.columns)

['account', 'sector', 'year_established', 'revenue', 'employees', 'office_location', 'subsidiary_of']
['Table', 'Field', 'Description']
['product', 'series', 'sales_price']
['opportunity_id', 'sales_agent', 'product', 'account', 'deal_stage', 'engage_date', 'close_date', 'close_value']
['sales_agent', 'manager', 'regional_office']


In [0]:
accounts_df = accounts_df.withColumnRenamed("subsidiary_of", "parent_company")
data_dictionary_df = data_dictionary_df.withColumnRenamed("Table", "table").withColumnRenamed("Field", "field").withColumnRenamed("Description", "description")

In [0]:
accounts_df.show(1)
data_dictionary_df.show(1)

+----------------+---------+----------------+-------+---------+---------------+--------------+
|         account|   sector|year_established|revenue|employees|office_location|parent_company|
+----------------+---------+----------------+-------+---------+---------------+--------------+
|Acme Corporation|technolgy|            1996|1100.04|     2822|  United States|          NULL|
+----------------+---------+----------------+-------+---------+---------------+--------------+
only showing top 1 row
+--------+-------+------------+
|   table|  field| description|
+--------+-------+------------+
|accounts|account|Company name|
+--------+-------+------------+
only showing top 1 row


In [0]:
null_accounts_df = accounts_df.select([sum(when(col(column).isNull(), 1).otherwise(0)).alias(column) for column in accounts_df.columns])

null_data_dictionary_df = data_dictionary_df.select([sum(when(col(column).isNull(), 1).otherwise(0)).alias(column) for column in data_dictionary_df.columns])

null_products_df = products_df.select([sum(when(col(column).isNull(), 1).otherwise(0)).alias(column) for column in products_df.columns])
 
null_sales_pipeline_df = sales_pipeline_df.select([sum(when(col(column).isNull(), 1).otherwise(0)).alias(column) for column in sales_pipeline_df.columns])

null_sales_teams_df = sales_teams_df.select([sum(when(col(column).isNull(), 1).otherwise(0)).alias(column) for column in sales_teams_df.columns])

display(null_accounts_df)
display(null_data_dictionary_df)
display(null_products_df)
display(null_sales_pipeline_df)
display(null_sales_teams_df)

account sector year_established revenue employees office_location subsidiary_of 0 0 0 0 0 0 70

Table Field Description 0 0 0

product series sales_price 0 0 0

opportunity_id sales_agent product account deal_stage engage_date close_date close_value 0 0 0 1425 0 500 2089 2089

sales_agent manager regional_office 0 0 0

In [0]:
sales_pipeline_df.display()
accounts_df.display()

opportunity_id sales_agent product account deal_stage engage_date close_date close_value 1C1I7A6R Moses Frase GTX Plus Basic Cancity Won 2016-10-20 2017-03-01 1054 Z063OYW0 Darcel Schlecht GTXPro Isdom Won 2016-10-25 2017-03-11 4514 EC4QE1BX Darcel Schlecht MG Special Cancity Won 2016-10-25 2017-03-07 50 MV1LWRNH Moses Frase GTX Basic Codehow Won 2016-10-25 2017-03-09 588 PE84CX4O Zane Levy GTX Basic Hatfan Won 2016-10-25 2017-03-02 517 ZNBS69V1 Anna Snelling MG Special Ron-tech Won 2016-10-29 2017-03-01 49 9ME3374G Vicki Laflamme MG Special J-Texon Won 2016-10-30 2017-03-02 57 7GN8Q4LL Markita Hansen GTX Basic Cheers Won 2016-11-01 2017-03-07 601 OLK9LKZB Niesha Huffines GTX Plus Basic Zumgoity Won 2016-11-01 2017-03-03 1026 HAXMC4IX James Ascencio MG Advanced null Engaging 2016-11-03 null null NL3JZH1Z Anna Snelling MG Special Bioholding Won 2016-11-04 2017-03-10 53 KWVA7VR1 Gladys Colclough GTXPro Genco Pura Olive Oil Company Lost 2016-11-04 2017-03-18 0 S8DX3XOU James Ascencio GTX Plus Pro Sunnamplex Won 2016-11-04 2017-03-10 5169 ENB2XD8G Maureen Marcano GTX Plus Pro Sonron Won 2016-11-04 2017-03-06 4631 09YE9QOV Hayden Neloms MG Advanced Finjob Won 2016-11-05 2017-03-11 3393 3F5MZNEH Rosalina Dieter MG Special Sonron Lost 2016-11-05 2017-03-03 0 M6WEJXC0 Rosalina Dieter MG Advanced Scotfind Won 2016-11-05 2017-03-06 3284 6PTR7VBR Versie Hillebrand MG Special Treequote Won 2016-11-06 2017-03-05 61 902REDPA Daniell Hammack GTXPro Xx-zobam Lost 2016-11-07 2017-03-09 0 5J9CMGDV Elease Gluck MG Special Rantouch Won 2016-11-07 2017-03-08 46 JJXRR8R6 James Ascencio GTX Plus Pro Fasehatice Lost 2016-11-07 2017-03-17 0 WF4HA5NW Moses Frase MG Special Ron-tech Won 2016-11-07 2017-03-18 50 C5K2JP1H Violet Mclelland GTX Plus Basic Vehement Capital Partners Won 2016-11-07 2017-03-11 1014 ADRB8OMB Darcel Schlecht GTX Basic Warephase Won 2016-11-08 2017-03-26 561 SBCR987L Kami Bicknell GTX Basic Zoomit Won 2016-11-10 2017-03-23 590 UP409DSB Maureen Marcano MG Advanced Ganjaflex Engaging 2016-11-10 null null JSD4APT2 Versie Hillebrand MG Special Bioholding Won 2016-11-10 2017-03-12 61 AO9Z2D17 Violet Mclelland GTX Plus Pro Xx-zobam Lost 2016-11-10 2017-03-11 0 5M58DTJK Elease Gluck MG Special Cheers Won 2016-11-11 2017-03-05 58 KNY1OSAB Maureen Marcano GTXPro Labdrill Won 2016-11-11 2017-03-14 4899 EAZDUUM9 Rosie Papadopoulos MG Advanced Zotware Lost 2016-11-11 2017-03-01 0 2STUSOFE Versie Hillebrand MG Special dambase Won 2016-11-11 2017-03-03 67 JYKM0B00 James Ascencio GTXPro Xx-holding Won 2016-11-12 2017-03-06 4338 KU28360J Kary Hendrixson GTX Basic Fasehatice Won 2016-11-12 2017-03-19 578 N4SD17JR Reed Clapper GTX Basic Acme Corporation Won 2016-11-12 2017-03-01 556 E67P9Y3Q Rosalina Dieter GTX Basic Green-Plus Won 2016-11-12 2017-03-03 635 AT3MMVIS Wilburn Farren MG Advanced The New York Inquirer Won 2016-11-12 2017-03-07 3045 REJ11LRY Garret Kinder GTX Plus Basic Mathtouch Won 2016-11-13 2017-03-14 1233 ERV0CAZ7 Versie Hillebrand MG Special Zumgoity Won 2016-11-13 2017-03-09 60 8SOQADK7 Anna Snelling MG Special Gogozoom Lost 2016-11-14 2017-03-30 0 TCHFT25B Darcel Schlecht GTX Basic Stanredtax Lost 2016-11-14 2017-03-08 0 CZVN09WN Darcel Schlecht GTX Plus Basic Konmatfix Won 2016-11-14 2017-03-20 1170 EG7OFLFR Kami Bicknell GTX Basic null Engaging 2016-11-14 null null 30UQWUKB Marty Freudenburg GTX Plus Basic Genco Pura Olive Oil Company Won 2016-11-15 2017-03-20 1162 OLVI7L8M Cassey Cress GTXPro null Engaging 2016-11-16 null null 97UN20YY Darcel Schlecht MG Advanced Conecom Won 2016-11-16 2017-03-14 3725 JXLERZ9O Kary Hendrixson GTX Basic Golddex Won 2016-11-16 2017-03-31 559 6ROE69W5 Rosalina Dieter GTX Basic Plexzap Lost 2016-11-16 2017-03-11 0 0DFXFKT7 Darcel Schlecht GTX Plus Basic Rundofase Lost 2016-11-17 2017-03-21 0 XKMZVSN4 James Ascencio GTX Plus Pro Sonron Won 2016-11-17 2017-03-05 4667 IU8V0BZK Marty Freudenburg GTX Plus Basic Finhigh Won 2016-11-17 2017-03-17 903 XY42936P Maureen Marcano GTX Plus Basic Finjob Won 20

account sector year_established revenue employees office_location subsidiary_of Acme Corporation technolgy 1996 1100.04 2822 United States null Betasoloin medical 1999 251.41 495 United States null Betatech medical 1986 647.18 1185 Kenya null Bioholding medical 2012 587.34 1356 Philipines null Bioplex medical 1991 326.82 1016 United States null Blackzim retail 2009 497.11 1588 United States null Bluth Company technolgy 1993 1242.32 3027 United States Acme Corporation Bubba Gump software 2002 987.39 2253 United States null Cancity retail 2001 718.62 2448 United States null Cheers entertainment 1993 4269.9 6472 United States Massive Dynamic Codehow software 1998 2714.9 2641 United States Acme Corporation Condax medical 2017 4.54 9 United States null Conecom technolgy 2005 1520.66 1806 United States null Dalttechnology software 2013 98.79 96 United States Bubba Gump dambase marketing 1995 2173.98 2928 United States Inity Domzoom entertainment 1998 217.87 551 United States null Doncon technolgy 2010 587.72 1501 United States null Donquadtech technolgy 1992 1712.68 3194 United States Acme Corporation Dontechi software 1982 4618.0 10083 United States null Donware marketing 1999 1197.44 2570 United States null Fasehatice retail 1990 4968.91 7523 United States null Faxquote telecommunications 1995 1825.82 5595 United States Sonron Finhigh finance 2006 1102.43 1759 United States null Finjob employment 1988 2059.9 3644 United States null Funholding finance 1991 2819.5 7227 United States Golddex Ganjaflex retail 1995 5158.71 17479 Japan null Gekko & Co retail 1990 2520.83 3502 United States null Genco Pura Olive Oil Company retail 2007 894.33 1635 Italy null Globex Corporation technolgy 2000 1223.72 2497 Norway null Gogozoom telecommunications 2007 86.68 187 United States Sonron Golddex finance 2008 52.5 165 United States null Goodsilron marketing 2000 2952.73 5107 United States null Green-Plus services 2003 692.19 1922 United States null Groovestreet retail 2003 223.8 299 United States null Hatfan services 1982 792.46 1299 United States null Hottechi technolgy 1997 8170.38 16499 Korea null Initech telecommunications 1994 6395.05 20275 United States null Inity marketing 1986 2403.58 8801 United States null Isdom medical 2002 3178.24 4540 United States null Iselectrics technolgy 2011 527.11 1428 United States Acme Corporation J-Texon retail 1989 1388.67 3583 United States null Kan-code software 1982 11698.03 34288 United States null Kinnamplus retail 2004 702.72 1831 United States null Konex technolgy 1980 7708.38 13756 United States null Konmatfix marketing 1985 375.43 1190 United States null Labdrill medical 1985 2741.37 9226 United States null Lexiqvolax medical 2004 1618.89 3889 United States null Massive Dynamic entertainment 1989 665.06 1095 United States null Mathtouch marketing 1984 3027.46 9516 Jordan null Nam-zim services 1987 405.59 1179 Brazil Warephase Newex services 1991 1012.72 3492 Germany null Ontomedia employment 1997 882.12 2769 United States null Opentech finance 1994 355.23 853 United States null Plexzap retail 2001 2437.85 4874 United States null Plusstrip entertainment 2002 349.81 315 United States null Plussunin retail 2003 1419.98 4018 United States null Rangreen technolgy 1987 2938.67 8775 Panama null Rantouch telecommunications 1994 1188.42 3015 United States null Ron-tech medical 1992 3922.42 6837 United States null Rundofase technolgy 1983 1008.06 1238 United States null Scotfind software 1996 6354.87 16780 United States Bubba Gump Scottech marketing 2012 45.39 100 United States Inity Silis medical 1994 2818.38 6290 United States null Singletechno retail 1996 2214.94 5374 United States null Sonron telecommunications 1999 1699.85 5108 United States null Stanredtax finance 1987 1698.2 3798 United States null Statholdings employment 1997 291.27 586 United States null Streethex retail 1988 1376.8 1165 Belgium null Sumace retail 2000 167.89 493 Romania null Sunnamplex marketing 2008 894.37 1593 Poland null The New 

In [0]:
accounts_df = accounts_df.fillna({
    "parent_company" : "independent"
})

sales_pipeline_df = sales_pipeline_df.fillna({
    "account": "unknown"
})



In [0]:
accounts_df.display()
sales_pipeline_df.display()

account sector year_established revenue employees office_location parent_company Acme Corporation technolgy 1996 1100.04 2822 United States independent Betasoloin medical 1999 251.41 495 United States independent Betatech medical 1986 647.18 1185 Kenya independent Bioholding medical 2012 587.34 1356 Philipines independent Bioplex medical 1991 326.82 1016 United States independent Blackzim retail 2009 497.11 1588 United States independent Bluth Company technolgy 1993 1242.32 3027 United States Acme Corporation Bubba Gump software 2002 987.39 2253 United States independent Cancity retail 2001 718.62 2448 United States independent Cheers entertainment 1993 4269.9 6472 United States Massive Dynamic Codehow software 1998 2714.9 2641 United States Acme Corporation Condax medical 2017 4.54 9 United States independent Conecom technolgy 2005 1520.66 1806 United States independent Dalttechnology software 2013 98.79 96 United States Bubba Gump dambase marketing 1995 2173.98 2928 United States Inity Domzoom entertainment 1998 217.87 551 United States independent Doncon technolgy 2010 587.72 1501 United States independent Donquadtech technolgy 1992 1712.68 3194 United States Acme Corporation Dontechi software 1982 4618.0 10083 United States independent Donware marketing 1999 1197.44 2570 United States independent Fasehatice retail 1990 4968.91 7523 United States independent Faxquote telecommunications 1995 1825.82 5595 United States Sonron Finhigh finance 2006 1102.43 1759 United States independent Finjob employment 1988 2059.9 3644 United States independent Funholding finance 1991 2819.5 7227 United States Golddex Ganjaflex retail 1995 5158.71 17479 Japan independent Gekko & Co retail 1990 2520.83 3502 United States independent Genco Pura Olive Oil Company retail 2007 894.33 1635 Italy independent Globex Corporation technolgy 2000 1223.72 2497 Norway independent Gogozoom telecommunications 2007 86.68 187 United States Sonron Golddex finance 2008 52.5 165 United States independent Goodsilron marketing 2000 2952.73 5107 United States independent Green-Plus services 2003 692.19 1922 United States independent Groovestreet retail 2003 223.8 299 United States independent Hatfan services 1982 792.46 1299 United States independent Hottechi technolgy 1997 8170.38 16499 Korea independent Initech telecommunications 1994 6395.05 20275 United States independent Inity marketing 1986 2403.58 8801 United States independent Isdom medical 2002 3178.24 4540 United States independent Iselectrics technolgy 2011 527.11 1428 United States Acme Corporation J-Texon retail 1989 1388.67 3583 United States independent Kan-code software 1982 11698.03 34288 United States independent Kinnamplus retail 2004 702.72 1831 United States independent Konex technolgy 1980 7708.38 13756 United States independent Konmatfix marketing 1985 375.43 1190 United States independent Labdrill medical 1985 2741.37 9226 United States independent Lexiqvolax medical 2004 1618.89 3889 United States independent Massive Dynamic entertainment 1989 665.06 1095 United States independent Mathtouch marketing 1984 3027.46 9516 Jordan independent Nam-zim services 1987 405.59 1179 Brazil Warephase Newex services 1991 1012.72 3492 Germany independent Ontomedia employment 1997 882.12 2769 United States independent Opentech finance 1994 355.23 853 United States independent Plexzap retail 2001 2437.85 4874 United States independent Plusstrip entertainment 2002 349.81 315 United States independent Plussunin retail 2003 1419.98 4018 United States independent Rangreen technolgy 1987 2938.67 8775 Panama independent Rantouch telecommunications 1994 1188.42 3015 United States independent Ron-tech medical 1992 3922.42 6837 United States independent Rundofase technolgy 1983 1008.06 1238 United States independent Scotfind software 1996 6354.87 16780 United States Bubba Gump Scottech marketing 2012 45.39 100 United States Inity Silis medical 1994 2818.38 6290 United States independent Singletechno retail 1996 2214.9

opportunity_id sales_agent product account deal_stage engage_date close_date close_value 1C1I7A6R Moses Frase GTX Plus Basic Cancity Won 2016-10-20 2017-03-01 1054 Z063OYW0 Darcel Schlecht GTXPro Isdom Won 2016-10-25 2017-03-11 4514 EC4QE1BX Darcel Schlecht MG Special Cancity Won 2016-10-25 2017-03-07 50 MV1LWRNH Moses Frase GTX Basic Codehow Won 2016-10-25 2017-03-09 588 PE84CX4O Zane Levy GTX Basic Hatfan Won 2016-10-25 2017-03-02 517 ZNBS69V1 Anna Snelling MG Special Ron-tech Won 2016-10-29 2017-03-01 49 9ME3374G Vicki Laflamme MG Special J-Texon Won 2016-10-30 2017-03-02 57 7GN8Q4LL Markita Hansen GTX Basic Cheers Won 2016-11-01 2017-03-07 601 OLK9LKZB Niesha Huffines GTX Plus Basic Zumgoity Won 2016-11-01 2017-03-03 1026 HAXMC4IX James Ascencio MG Advanced unknown Engaging 2016-11-03 null null NL3JZH1Z Anna Snelling MG Special Bioholding Won 2016-11-04 2017-03-10 53 KWVA7VR1 Gladys Colclough GTXPro Genco Pura Olive Oil Company Lost 2016-11-04 2017-03-18 0 S8DX3XOU James Ascencio GTX Plus Pro Sunnamplex Won 2016-11-04 2017-03-10 5169 ENB2XD8G Maureen Marcano GTX Plus Pro Sonron Won 2016-11-04 2017-03-06 4631 09YE9QOV Hayden Neloms MG Advanced Finjob Won 2016-11-05 2017-03-11 3393 3F5MZNEH Rosalina Dieter MG Special Sonron Lost 2016-11-05 2017-03-03 0 M6WEJXC0 Rosalina Dieter MG Advanced Scotfind Won 2016-11-05 2017-03-06 3284 6PTR7VBR Versie Hillebrand MG Special Treequote Won 2016-11-06 2017-03-05 61 902REDPA Daniell Hammack GTXPro Xx-zobam Lost 2016-11-07 2017-03-09 0 5J9CMGDV Elease Gluck MG Special Rantouch Won 2016-11-07 2017-03-08 46 JJXRR8R6 James Ascencio GTX Plus Pro Fasehatice Lost 2016-11-07 2017-03-17 0 WF4HA5NW Moses Frase MG Special Ron-tech Won 2016-11-07 2017-03-18 50 C5K2JP1H Violet Mclelland GTX Plus Basic Vehement Capital Partners Won 2016-11-07 2017-03-11 1014 ADRB8OMB Darcel Schlecht GTX Basic Warephase Won 2016-11-08 2017-03-26 561 SBCR987L Kami Bicknell GTX Basic Zoomit Won 2016-11-10 2017-03-23 590 UP409DSB Maureen Marcano MG Advanced Ganjaflex Engaging 2016-11-10 null null JSD4APT2 Versie Hillebrand MG Special Bioholding Won 2016-11-10 2017-03-12 61 AO9Z2D17 Violet Mclelland GTX Plus Pro Xx-zobam Lost 2016-11-10 2017-03-11 0 5M58DTJK Elease Gluck MG Special Cheers Won 2016-11-11 2017-03-05 58 KNY1OSAB Maureen Marcano GTXPro Labdrill Won 2016-11-11 2017-03-14 4899 EAZDUUM9 Rosie Papadopoulos MG Advanced Zotware Lost 2016-11-11 2017-03-01 0 2STUSOFE Versie Hillebrand MG Special dambase Won 2016-11-11 2017-03-03 67 JYKM0B00 James Ascencio GTXPro Xx-holding Won 2016-11-12 2017-03-06 4338 KU28360J Kary Hendrixson GTX Basic Fasehatice Won 2016-11-12 2017-03-19 578 N4SD17JR Reed Clapper GTX Basic Acme Corporation Won 2016-11-12 2017-03-01 556 E67P9Y3Q Rosalina Dieter GTX Basic Green-Plus Won 2016-11-12 2017-03-03 635 AT3MMVIS Wilburn Farren MG Advanced The New York Inquirer Won 2016-11-12 2017-03-07 3045 REJ11LRY Garret Kinder GTX Plus Basic Mathtouch Won 2016-11-13 2017-03-14 1233 ERV0CAZ7 Versie Hillebrand MG Special Zumgoity Won 2016-11-13 2017-03-09 60 8SOQADK7 Anna Snelling MG Special Gogozoom Lost 2016-11-14 2017-03-30 0 TCHFT25B Darcel Schlecht GTX Basic Stanredtax Lost 2016-11-14 2017-03-08 0 CZVN09WN Darcel Schlecht GTX Plus Basic Konmatfix Won 2016-11-14 2017-03-20 1170 EG7OFLFR Kami Bicknell GTX Basic unknown Engaging 2016-11-14 null null 30UQWUKB Marty Freudenburg GTX Plus Basic Genco Pura Olive Oil Company Won 2016-11-15 2017-03-20 1162 OLVI7L8M Cassey Cress GTXPro unknown Engaging 2016-11-16 null null 97UN20YY Darcel Schlecht MG Advanced Conecom Won 2016-11-16 2017-03-14 3725 JXLERZ9O Kary Hendrixson GTX Basic Golddex Won 2016-11-16 2017-03-31 559 6ROE69W5 Rosalina Dieter GTX Basic Plexzap Lost 2016-11-16 2017-03-11 0 0DFXFKT7 Darcel Schlecht GTX Plus Basic Rundofase Lost 2016-11-17 2017-03-21 0 XKMZVSN4 James Ascencio GTX Plus Pro Sonron Won 2016-11-17 2017-03-05 4667 IU8V0BZK Marty Freudenburg GTX Plus Basic Finhigh Won 2016-11-17 2017-03-17 903 XY42936P Maureen Marcano GTX Plus Basic Finj

In [0]:
null_accounts_df = accounts_df.select([sum(when(col(column).isNull(), 1).otherwise(0)).alias(column) for column in accounts_df.columns])
null_accounts_df.show()

+-------+------+----------------+-------+---------+---------------+--------------+
|account|sector|year_established|revenue|employees|office_location|parent_company|
+-------+------+----------------+-------+---------+---------------+--------------+
|      0|     0|               0|      0|        0|              0|             0|
+-------+------+----------------+-------+---------+---------------+--------------+



In [0]:
null_sales_pipeline_df = sales_pipeline_df.select([sum(when(col(column).isNull(), 1).otherwise(0)).alias(column) for column in sales_pipeline_df.columns])
null_sales_pipeline_df.show()

---------------------------------------------------------------------------
NameError                                 Traceback (most recent call last)
File <command-4735821366776745>, line 1
----> 1 null_sales_pipeline_df = sales_pipeline_df.select([sum(when(col(column).isNull(), 1).otherwise(0)).alias(column) for column in sales_pipeline_df.columns])
      2 null_sales_pipeline_df.show()

NameError: name 'sales_pipeline_df' is not defined

In [0]:
accounts_df.write.option("header", "true").csv("/mnt/transformed-data/accounts.csv")
data_dictionary_df.write.option("header", "true").csv("/mnt/transformed-data/data_dictionary.csv")
products_df.write.option("header", "true").csv("/mnt/transformed-data/products.csv")
sales_pipeline_df.write.option("header", "true").csv("/mnt/transformed-data/sales_pipeline.csv")
sales_teams_df.write.option("header", "true").csv("/mnt/transformed-data/sales_teams.csv")